In [ ]:
#Leon main file 

In [1]:
#Loading all the needed Packages
import pandas as pd
import numpy as np
import gurobipy as gp
from gurobipy import GRB

In [3]:
# Load all CSV files
Demand_Data_Normalized = pd.read_csv('../Data/ModelData/Demand_YearlyDemandUtilityProfile_Normalized.csv', delimiter=',')
Fuel_Cost_Data_Normalized = pd.read_csv('../Data/ModelData/FuelCost_PriceDevelopment50years.csv', delimiter=',')
Generation_Data_Normalized = pd.read_csv('../Data/ModelData/VRE_YearlyGenerationProfile_Normalized.csv', delimiter=',')
Generation_Asset_Data_Existing = pd.read_csv('../Data/ModelData/Generators_AssetData_Existing.csv', delimiter=',')
Demand_Unit_Data = pd.read_csv('../Data/ModelData/Demand_UnitSpecificData.csv', delimiter=',')
System_Demand = pd.read_csv('../Data/ModelData/System_Demand.csv', delimiter=',')
Transmission_Capacity = pd.read_csv('../Data/ModelData/Transmission Capacity.csv', delimiter=',')
Fuel_Cost_Absolute = pd.read_csv('../Data/ModelData/Fuel_Cost_Absolute.csv', delimiter=',')
Demand_Developement = pd.read_csv('../Data/ModelData/Demand_Development.csv', delimiter=',')

In [4]:
Number_of_Seasons = 5
Number_of_Years = 30
Number_of_Generators= len(Generation_Asset_Data_Existing)
Number_of_Demand_Units = len(Demand_Unit_Data)
Number_of_Price_Zones = 2
Number_of_Hours = 24

In [11]:
#Creating a function for the market clearing

def MarketClearingProblem1(Demand_Data_Normalized,
                           Fuel_Cost_Data_Normalized,
                           Generation_Data_Normalized,
                           Generation_Asset_Data_Existing,
                           Demand_Unit_Data,
                           System_Demand,
                           Transmission_Capacity,
                           Season,
                           Number_of_Price_Zones,
                           Number_of_Hours,
                           year):


    model = gp.Model("MarketClearingProblem1")

    # #Defining some iput data

    # #Define the number of generators by taking the length of the Generation_Asset_Data_Existing file
    Number_of_Generators = len(Generation_Asset_Data_Existing)
    Number_of_Demand_Units = len(Demand_Unit_Data)
    Number_of_Transmission_Lines = len(Transmission_Capacity)
    # #-----------------------------------------------------------------------------------------------------------------

    # #Data Handling to get daily demand

    # Filter Demand_Data_Normalized by the given season
    season_data = Demand_Data_Normalized[Demand_Data_Normalized['Season'] == Season]

    # Create a empty DataFrames to store the results, with 24 columns for each hour
    Daily_Demand_Normalized = pd.DataFrame(columns=[f'Hour_{i+1}' for i in range(24)])
    Daily_Demand_Utility = pd.DataFrame(columns=[f'Hour_{i+1}' for i in range(24)])

    # Loop through each row in Demand_Unit_Data
    for _, row in Demand_Unit_Data.iterrows():
        load_type = row['LoadType'].strip() # Load type (e.g., 'U_Residential', 'U_IndustryBase', 'U_IndustryPeak')
        utility_type = row['UtilityType'].strip()
        percent_load = row['% of system load'] / 100
        
        # Check if the load type exists in the Demand_Data_Normalized columns
        if load_type in season_data.columns:
            # Retrieve the hourly values for the specified load type and scale them
            hourly_values_loadtype = season_data[season_data['Hour'] <= 24][load_type].values * percent_load
            
            # Create a new row with these hourly values
            row_data = pd.DataFrame([hourly_values_loadtype], columns=[f'Hour_{i+1}' for i in range(24)])
            
            # Add identifying columns (like Load #, Zone, and LoadType) for clarity
            # row_data['Load #'] = row['Load #']
            # row_data['Zone'] = row['Zone']
            # row_data['LoadType'] = load_type
            
            # Append the new row to the result_data DataFrame
            Daily_Demand_Normalized = pd.concat([Daily_Demand_Normalized, row_data], ignore_index=True)
        # Check if the utility type exists in the Demand_Data_Normalized columns
        if utility_type in season_data.columns:
            # Retrieve the hourly values for the specified load type and scale them
            hourly_values_utilitytype = season_data[season_data['Hour'] <= 24][utility_type].values 
            
            # Create a new row with these hourly values
            row_data = pd.DataFrame([hourly_values_utilitytype], columns=[f'Hour_{i+1}' for i in range(24)])
            
            # Add identifying columns (like Load #, Zone, and LoadType) for clarity
            # row_data['Load #'] = row['Load #']
            # row_data['Zone'] = row['Zone']
            # row_data['LoadType'] = utility_type
            
            # Append the new row to the result_data DataFrame
            Daily_Demand_Utility = pd.concat([Daily_Demand_Utility, row_data], ignore_index=True)

    # Reset index and inspect result
    Daily_Demand_Normalized.reset_index(drop=True, inplace=True)
    Daily_Demand_Utility.reset_index(drop=True, inplace=True)


    #getting from normalized load to absolute load values
    Daily_Demand_Absolute = pd.DataFrame(
        index=range(len(Daily_Demand_Normalized)),  # Set the number of rows
        columns=[f'Hour_{i+1}' for i in range(24)]  # Set the columns for each hour
    )
    for l in range(len(Daily_Demand_Normalized)):
            for h in range(len(System_Demand)):
                Daily_Demand_Absolute.iloc[l,h] = Daily_Demand_Normalized.iloc[l,h]*System_Demand['System demand (MW)'].iloc[h]





    # #-----------------------------------------------------------------------------------------------------------------

    #Defining the decision variables

    # Defining a variable for the generators day ahead bid
    Gen_DABid = model.addVars(Number_of_Generators,Number_of_Hours, vtype=GRB.CONTINUOUS, name="Gen_DABid")
        # Defining a variable for the demand day ahead bid
    Dem_DABid = model.addVars(Number_of_Demand_Units,Number_of_Hours, vtype=GRB.CONTINUOUS, name="Dem_DABid")
    # Define voltage angle variables for each zone
    Voltage_Angle = model.addVars(Number_of_Price_Zones,Number_of_Hours, vtype=GRB.CONTINUOUS, name="Voltage_Angle")
    # Define power flow variables (as before, but now dependent on voltage angles)
    Power_Flow = model.addVars(Number_of_Transmission_Lines,Number_of_Hours, vtype=GRB.CONTINUOUS, lb=-GRB.INFINITY, name="Power_Flow")

    #Define a ancilary variable for power outflow of zone
    Outflow_Zone = model.addVars(Number_of_Price_Zones,Number_of_Hours, vtype=GRB.CONTINUOUS, name="Outflow_Zone")
    Inflow_Zone = model.addVars(Number_of_Price_Zones,Number_of_Hours, vtype=GRB.CONTINUOUS, name="Inflow_Zone")

    # #-----------------------------------------------------------------------------------------------------------------

    # #Defining objective function

    #Objective function that maximizes social welfare
    objective = ( gp.quicksum(Daily_Demand_Utility.iloc[d,h] * Dem_DABid[d,h] for d in range(Number_of_Demand_Units) for h in range(Number_of_Hours)) -
                gp.quicksum(Generation_Asset_Data_Existing['C_i ($/MWh)'].iloc[g] * Gen_DABid[g,h] for g in range(Number_of_Generators) for h in range(Number_of_Hours)))
    model.setObjective(objective, GRB.MAXIMIZE)

    #-----------------------------------------------------------------------------------------------------------------

    #Defining Constraints

    #Defining maximium Production Capacity

    for p in range(Number_of_Generators):
        for h in range(Number_of_Hours):
            model.addConstr(Gen_DABid[p,h] <= Generation_Asset_Data_Existing['P_max current (MW)'].iloc[p], name=f"Production_Capacity_Constraint_{p,h}")

    #Defining maximum Demand 
    for d in range(Number_of_Demand_Units):
        for h in range(Number_of_Hours):
            model.addConstr(Dem_DABid[d,h] <= Daily_Demand_Absolute.iloc[d,h], name=f"Demand_Capacity_Constraint_{d,h}")

    #Defining the power flow

    for tr in range(Number_of_Transmission_Lines):
        for h in range(Number_of_Hours):
            from_Zone = Transmission_Capacity['FromZone'][tr]  
            to_Zone = Transmission_Capacity['ToZone'][tr]  
            reactance = Transmission_Capacity['Reactance'][tr]
            
            # Flow is proportional to the voltage angle difference divided by the reactance
            model.addConstr(
                Power_Flow[tr,h] == (Voltage_Angle[from_Zone,h] - Voltage_Angle[to_Zone,h]) / reactance,
                name=f"Flow_Equation_{from_Zone}_{to_Zone}"
            )

    # Constrain the power flow to be within the capacity of the transmission line
    for tr in range(Number_of_Transmission_Lines):
        for h in range(Number_of_Hours):
            capacity = Transmission_Capacity['Capacity [MW]'][tr]
            model.addConstr(Power_Flow[tr,h] <= capacity, name=f"Flow_Capacity_Constraint_Upper_{tr,h}")
            model.addConstr(Power_Flow[tr,h] >= -capacity, name=f"Flow_Capacity_Constraint_Lower_{tr,h}")



    # Update the power balance constraint for each node
    for zone in range(Number_of_Price_Zones):
        for h in range(Number_of_Hours):
            # Get the demand for the Zone
            demand_at_zone = gp.quicksum(
                Dem_DABid[d,h] 
                for d in range(Number_of_Demand_Units) 
                if Demand_Unit_Data['Zone'][d] == zone
            )
            
            # Get the production for this zone
            production_at_zone = gp.quicksum(
                Gen_DABid[p,h] for p in range(Number_of_Generators)
                if Generation_Asset_Data_Existing['Zone'][p] == zone
            )
            
            # Power flows into the zone (from other zones)
            Inflow_Zone = gp.quicksum(
                Power_Flow[tr,h] for tr in range(len(Transmission_Capacity))
                if Transmission_Capacity['ToZone'][tr] == zone
            )
            
            # Power flows out of the node (to other nodes)
            Outflow_Zone = gp.quicksum(
                Power_Flow[tr,h] for tr in range(len(Transmission_Capacity))
                if Transmission_Capacity['FromZone'][tr] == zone
            )
            
            # Add the power balance constraint: Production + Inflow = Demand + Outflow
            model.addConstr(demand_at_zone + Outflow_Zone == production_at_zone + Inflow_Zone, 
                            name=f"Power_Balance_Constraint_{zone,h}")
        
    model.optimize()


    # # Check optimization result
    #if model.status == GRB.INFEASIBLE:
        #print("Model is infeasible.")
    #elif model.status == GRB.UNBOUNDED:
        #print("Model is unbounded.")
    #elif model.status == GRB.TIME_LIMIT:
        #print("Time limit reached.")
    if model.status == GRB.OPTIMAL:
        #print("Optimal solution found.")
        TotalCost = model.objVal
        #print("Total Cost:",TotalCost)
        # Print the value of the Production variables
        #print("Production values:")

        # Creating an empty data frame to store the results of the model
        Daily_Results = pd.DataFrame(columns=["Year", "Season", "Hour", "Zone", "MCP"])

        # Assuming Season is defined, and Daily_Results is an empty DataFrame with the correct columns
        for h in range(Number_of_Hours):
            for zone in range(Number_of_Price_Zones):
                # Create a dictionary to store the row data for the current hour and zone
                row_data = {"Year": year, "Season": Season, "Hour": h, "Zone": zone}

                # Retrieve the dual value of the Power Balance constraint for the current zone and hour
                constr_name = f"Power_Balance_Constraint_{zone,h}"
                constr = model.getConstrByName(constr_name)

                if constr:
                    # Store the dual value (Day Ahead Price) in the row data dictionary
                    row_data["MCP"] = constr.Pi

                # Append the row data to the DataFrame as a new row
                Daily_Results = pd.concat([Daily_Results, pd.DataFrame([row_data])], ignore_index=True)

            

            


        # # Print the value of the Voltage_Angle variables
        # print("/nVoltage Angle values:")
        # for n in range(Number_of_Nodes):
        #     print(f"Voltage_Angle[{n}] = {Voltage_Angle[n].X}")

        # Print the value of the Power_Flow variables
        # print("/nPower Flow values:")
        # for t in range(len(Transmission_Capacity)):
        #     print(f"Power_Flow[{t}] = {Power_Flow[t].X}")

    return Daily_Results









In [12]:
def LongTermMarketResults(Demand_Data_Normalized,
                           Fuel_Cost_Data_Normalized,
                           Generation_Data_Normalized,
                           Generation_Asset_Data_Existing,
                           Demand_Unit_Data,
                           System_Demand,
                           Transmission_Capacity,
                           Demand_Developement,
                           Number_of_Price_Zones,
                           Number_of_Generators,
                           Number_of_Demand_Units,
                           Number_of_Years,
                           Number_of_Seasons,
                           Number_of_Hours):
    
    Yearly_Season_Daily_Results = pd.DataFrame()
    Generation_Asset_Data_Existing_Adjusted = Generation_Asset_Data_Existing
    Demand_Data_Normalized_Adjusted = Demand_Data_Normalized

    for y in range(Number_of_Years):
        #Adjusting the cost for generation unit based on price development
        for g in range(Number_of_Generators):
            if Generation_Asset_Data_Existing_Adjusted['Technology'][g] == "Coal":
                Generation_Asset_Data_Existing_Adjusted['C_i ($/MWh)'][g] = Generation_Asset_Data_Existing_Adjusted['C_i ($/MWh)'][g] * Fuel_Cost_Data_Normalized['Coal'][y] + Generation_Asset_Data_Existing_Adjusted['Emission Facor [t/MWh]'][g] * Fuel_Cost_Data_Normalized['Co2'][g]
            if Generation_Asset_Data_Existing_Adjusted['Technology'][g] == "Gas":
                Generation_Asset_Data_Existing_Adjusted['C_i ($/MWh)'][g] = Generation_Asset_Data_Existing_Adjusted['C_i ($/MWh)'][g] * Fuel_Cost_Data_Normalized['Gas'][y] + Generation_Asset_Data_Existing_Adjusted['Emission Facor [t/MWh]'][g] * Fuel_Cost_Data_Normalized['Co2'][g]
        for d in range(Number_of_Demand_Units):
            Demand_Data_Normalized_Adjusted['D_Residential'][d] = Demand_Developement['D_Residential'][y]
            Demand_Data_Normalized_Adjusted['D_IndustryBase'][d] = Demand_Developement['D_IndustryBase'][y]
            Demand_Data_Normalized_Adjusted['D_ IndustryPeak'][d] = Demand_Developement['D_ IndustryPeak'][y]
            
                    
        for s in range(Number_of_Seasons):
            Daily_Results = MarketClearingProblem1(
                                    Demand_Data_Normalized_Adjusted,
                                Fuel_Cost_Data_Normalized,
                                Generation_Data_Normalized,
                                Generation_Asset_Data_Existing_Adjusted,
                                Demand_Unit_Data,
                                System_Demand,
                                Transmission_Capacity,
                                s,
                                Number_of_Price_Zones,
                                Number_of_Hours,
                                y)
            Yearly_Season_Daily_Results = pd.concat([Yearly_Season_Daily_Results, Daily_Results], ignore_index=True)
    return Yearly_Season_Daily_Results

In [13]:
Yearly_Season_Daily_Results = LongTermMarketResults(Demand_Data_Normalized,
                           Fuel_Cost_Data_Normalized,
                           Generation_Data_Normalized,
                           Generation_Asset_Data_Existing,
                           Demand_Unit_Data,
                           System_Demand,
                           Transmission_Capacity,
                           Demand_Developement,
                           Number_of_Price_Zones,
                           Number_of_Generators,
                           Number_of_Demand_Units,
                           Number_of_Years,
                           Number_of_Seasons,
                           Number_of_Hours)

Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Intel(R) Core(TM) i7-1065G7 CPU @ 1.30GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 984 rows, 984 columns and 1920 nonzeros
Model fingerprint: 0xff89382c
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [5e+00, 1e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [4e+01, 6e+02]
Presolve removed 936 rows and 862 columns
Presolve time: 0.00s
Presolved: 48 rows, 122 columns, 146 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.9860026e+07   2.000728e+03   0.000000e+00      0s
      48    1.9523227e+07   0.000000e+00   0.000000e+00      0s

Solved in 48 iterations and 0.01 seconds (0.00 work units)
Optimal objective  1.952322690e+07
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Inte

C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\1086864082.py:24: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  Generation_Asset_Data_Existing_Adjusted['C_i ($/MWh)'][g] = Generation_Asset_Data_Existing_Adjusted['C_i ($/MWh)'][g] * Fuel_Cos

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.4453608e+07   1.107901e+03   0.000000e+00      0s
      42    1.4294401e+07   0.000000e+00   0.000000e+00      0s

Solved in 42 iterations and 0.02 seconds (0.00 work units)
Optimal objective  1.429440141e+07
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Intel(R) Core(TM) i7-1065G7 CPU @ 1.30GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 984 rows, 984 columns and 1920 nonzeros
Model fingerprint: 0x9e99435f
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [5e+00, 1e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 6e+02]
Presolve removed 945 rows and 838 columns
Presolve time: 0.01s
Presolved: 39 rows, 146 columns, 161 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    7.4147562e+06   1.4695

C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Results = pd.concat([Daily_Results, pd.DataFrame([row_data])], ignore_index=True)
C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:55: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Demand_Normalized = pd.concat([Daily_Demand_Normalized, row_data], ignore_index=True)
C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavi

Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Intel(R) Core(TM) i7-1065G7 CPU @ 1.30GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 984 rows, 984 columns and 1920 nonzeros
Model fingerprint: 0xc86763ce
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [5e+00, 1e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [9e+00, 6e+02]
Presolve removed 944 rows and 842 columns
Presolve time: 0.00s
Presolved: 40 rows, 142 columns, 158 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    7.5250969e+06   1.469015e+03   0.000000e+00      0s
      40    7.2943094e+06   0.000000e+00   0.000000e+00      0s

Solved in 40 iterations and 0.00 seconds (0.00 work units)
Optimal objective  7.294309369e+06
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Inte

...

C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Results = pd.concat([Daily_Results, pd.DataFrame([row_data])], ignore_index=True)
C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:55: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Demand_Normalized = pd.concat([Daily_Demand_Normalized, row_data], ignore_index=True)
C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavi

Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Intel(R) Core(TM) i7-1065G7 CPU @ 1.30GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 984 rows, 984 columns and 1920 nonzeros
Model fingerprint: 0x91919236
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [5e+00, 1e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 6e+02]
Presolve removed 936 rows and 879 columns
Presolve time: 0.02s
Presolved: 48 rows, 105 columns, 129 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    6.8200187e+06   1.546302e+03   0.000000e+00      0s
      48    6.5058458e+06   0.000000e+00   0.000000e+00      0s

Solved in 48 iterations and 0.02 seconds (0.00 work units)
Optimal objective  6.505845813e+06
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Inte

C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Results = pd.concat([Daily_Results, pd.DataFrame([row_data])], ignore_index=True)
C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:55: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Demand_Normalized = pd.concat([Daily_Demand_Normalized, row_data], ignore_index=True)
C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavi

Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Intel(R) Core(TM) i7-1065G7 CPU @ 1.30GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 984 rows, 984 columns and 1920 nonzeros
Model fingerprint: 0x627461d0
Coefficient statistics:
  Matrix range     [1e+00, 3e+00]
  Objective range  [5e+00, 1e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 6e+02]
Presolve removed 936 rows and 878 columns
Presolve time: 0.00s
Presolved: 48 rows, 106 columns, 130 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.6347264e+07   1.584777e+03   0.000000e+00      0s
      48    1.5924244e+07   0.000000e+00   0.000000e+00      0s

Solved in 48 iterations and 0.00 seconds (0.00 work units)
Optimal objective  1.592424365e+07


C:\Users\leonr\AppData\Local\Temp\ipykernel_8812\2672279125.py:221: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  Daily_Results = pd.concat([Daily_Results, pd.DataFrame([row_data])], ignore_index=True)


In [17]:
#Load csv files 
HourlyMCP = Yearly_Season_Daily_Results
Fuel_Cost_Forecast_Normalized = pd.read_csv('../Data/ModelData/FuelCost_PriceDevelopment50years.csv', delimiter=',')
Generation_Asset_Data_New = pd.read_csv('../Data/ModelData/Generators_AssetData_New.csv', delimiter=',')
VRE_Generation_profile = pd.read_csv('../Data/ModelData/VRE_YearlyGenerationProfile_Normalized.csv', delimiter=',')
Fuel_Cost_Absolute = pd.read_csv('../Data/ModelData/Fuel_Cost_Absolute.csv', delimiter=',')

#Define budget 
budget = 10000000000

In [18]:
#Define modelling time horizon
#Amount of years based on HourlyMCP data
Y = HourlyMCP['Year'].nunique()

#Amount of seasons in a year based on HourlyMCP data
S = HourlyMCP['Season'].nunique()

#Amount of hours in a season
H = HourlyMCP['Hour'].nunique()

#Print the amount of years, seasons and hours
print("Amount of years: ", Y)
print("Amount of seasons: ", S)
print("Amount of hours in a season: ", H)

Amount of years:  30
Amount of seasons:  5
Amount of hours in a season:  24


In [19]:
# Initialize the model
m = gp.Model("InvestmentModel")

# Define the decision variables
Inv_NewCap = m.addVars(Generation_Asset_Data_New['Unit #'], vtype=GRB.CONTINUOUS, name="Inv_NewCap")
P_NewCap = m.addVars(Generation_Asset_Data_New['Unit #'], Y, S, H, vtype=GRB.CONTINUOUS, name="P_NewCap")

# Define the objective function
profit = gp.quicksum(
    P_NewCap[i, y, s, h] * (
        HourlyMCP.loc[
            (HourlyMCP['Year'] == y) & 
            (HourlyMCP['Season'] == s) & 
            (HourlyMCP['Hour'] == h) & 
            (HourlyMCP['Zone'] == Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'Zone'].values[0]), 
            'MCP'].values[0] - 
        Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'C_i ($/MWh)'].values[0] *
        Fuel_Cost_Forecast_Normalized.loc[Fuel_Cost_Forecast_Normalized['Year'] == y, Generation_Asset_Data_New.loc[Generation_Asset_Data_New["Unit #"] == i, "Technology"].values[0]].values[0] - 
        Fuel_Cost_Absolute.loc[Fuel_Cost_Absolute['Cost Type'] == 'Co2', 'Cost'].values[0] *
        Fuel_Cost_Forecast_Normalized.loc[Fuel_Cost_Forecast_Normalized['Year'] == y, 'Co2'].values[0] *
        Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'Emission Facor [t/MWh]'].values[0]
    )
    for i in Generation_Asset_Data_New['Unit #']
    for y in range(Y)
    for s in range(S)
    for h in range(H)
)

investment_cost = gp.quicksum(
    Inv_NewCap[i] * Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'C_CapInv ($/MW)'].values[0]
    for i in Generation_Asset_Data_New['Unit #']
)

m.setObjective(73 * profit - investment_cost, GRB.MAXIMIZE)

# Define the constraints
m.addConstrs(
    (Inv_NewCap[i] <= Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'MaxInv (MW)'].values[0] for i in Generation_Asset_Data_New['Unit #']), 
    "InvestmentMax"
)

m.addConstr(
    gp.quicksum(Inv_NewCap[i] * Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'C_CapInv ($/MW)'].values[0] for i in Generation_Asset_Data_New['Unit #']) <= budget, 
    "Budget"
)

m.addConstrs(
    (P_NewCap[i, y, s, h] <= Inv_NewCap[i] for i in Generation_Asset_Data_New['Unit #'] for y in range(Y) for s in range(S) for h in range(H)), 
    "GenMax"
)

m.addConstrs(
    (P_NewCap[i, y, s, h] <= Inv_NewCap[i] * VRE_Generation_profile.loc[
        (VRE_Generation_profile['Hour'] == h) & 
        (VRE_Generation_profile['Season'] == s), 
        f'PVZ{Generation_Asset_Data_New.loc[Generation_Asset_Data_New["Unit #"] == i, "Zone"].values[0]}'
    ].values[0]
    for i in Generation_Asset_Data_New['Unit #'] if Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'Technology'].values[0] == 'PV'
    for y in range(Y) for s in range(S) for h in range(H)), 
    "PVGenMax"
)

m.addConstrs(
    (P_NewCap[i, y, s, h] <= Inv_NewCap[i] * VRE_Generation_profile.loc[
        (VRE_Generation_profile['Hour'] == h) & 
        (VRE_Generation_profile['Season'] == s), 
        f'WindZ{Generation_Asset_Data_New.loc[Generation_Asset_Data_New["Unit #"] == i, "Zone"].values[0]}'
    ].values[0]
    for i in Generation_Asset_Data_New['Unit #'] if Generation_Asset_Data_New.loc[Generation_Asset_Data_New['Unit #'] == i, 'Technology'].values[0] == 'Wind'
    for y in range(Y) for s in range(S) for h in range(H)), 
    "WindGenMax"
)

# Solve the model
m.optimize()

# Check if the model found an optimal solution
if m.status == GRB.OPTIMAL:
    # Print the optimal solution
    for v in m.getVars():
        print('%s %g' % (v.varName, v.x))
    print('Obj:', m.objVal)
else:
    print("No optimal solution found. Status code:", m.status)

# Save the optimal solution to a DataFrame
df1 = pd.DataFrame({
    'Unit #': Generation_Asset_Data_New['Unit #'],
    'Investment': [Inv_NewCap[i].x for i in Generation_Asset_Data_New['Unit #']]
})

df2 = pd.DataFrame({
    'Unit #': [i for i in Generation_Asset_Data_New['Unit #'] for y in range(Y) for s in range(S) for h in range(H)],
    'Year': [y for i in Generation_Asset_Data_New['Unit #'] for y in range(Y) for s in range(S) for h in range(H)],
    'Season': [s for i in Generation_Asset_Data_New['Unit #'] for y in range(Y) for s in range(S) for h in range(H)],
    'Hour': [h for i in Generation_Asset_Data_New['Unit #'] for y in range(Y) for s in range(S) for h in range(H)],
    'Generation': [P_NewCap[i, y, s, h].x for i in Generation_Asset_Data_New['Unit #'] for y in range(Y) for s in range(S) for h in range(H)]
})

print(df1)
print(df2)


Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (win64 - Windows 11.0 (22631.2))

CPU model: Intel(R) Core(TM) i7-1065G7 CPU @ 1.30GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 82817 rows, 57616 columns and 162092 nonzeros
Model fingerprint: 0x9dad2fad
Coefficient statistics:
  Matrix range     [4e-04, 2e+06]
  Objective range  [4e+02, 2e+06]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+02, 1e+10]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Presolve removed 39497 rows and 35949 columns
Presolve time: 0.07s
Presolved: 43320 rows, 21667 columns, 86640 nonzeros

Concurrent LP optimizer: dual simplex and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier statistics:
 Dense cols : 4
 AA' NZ     : 1.589e+04
 Factor NZ  : 2.648e+04 (roughly 7 MB of memory)
 Factor Ops : 6.885e+04 (less than 1 second per it